In [0]:
from pyspark.sql import SparkSession
import getpass
username = getpass.getuser()
spark = SparkSession \
    .builder \
        .appName("Financial Transaction") \
            .config("spark.ui.port","0") \
                .config("spark.sql.warehouse.dir",f"/user/{username}/warehouse") \
                    .enableHiveSupport() \
                        .master("yarn") \
                            .getOrCreate()

In [0]:
from pyspark.sql.types import *
transaction_schema = StructType([
    StructField("id",IntegerType()),
    StructField("date",TimestampType()),
    StructField("client_id",IntegerType()),
    StructField("card_id", IntegerType()),
    StructField("amount", StringType()),
    StructField("use_chip", StringType()),
    StructField("Merchent_id", IntegerType()),
    StructField("merchent_city",StringType()),
    StructField("merchent_state",StringType()),
    StructField("zip", DoubleType()),
    StructField("mcc", IntegerType()),
    StructField("error", StringType())
])

In [0]:
transaction_raw_df = spark.read \
    .format("csv") \
        .schema(transaction_schema) \
            .load("dbfs:/FileStore/FinancialTransaction/transaction_raw")

In [0]:
transaction_raw_df.show(truncate=False)

+-------+-------------------+---------+-------+-------+------------------+-----------+---------------+--------------+-------+----+-----+
|id     |date               |client_id|card_id|amount |use_chip          |Merchent_id|merchent_city  |merchent_state|zip    |mcc |error|
+-------+-------------------+---------+-------+-------+------------------+-----------+---------------+--------------+-------+----+-----+
|7475327|2010-01-01 00:01:00|1556     |2972   |$-77.00|Swipe Transaction |59935      |Beulah         |ND            |58523.0|5499|null |
|7475328|2010-01-01 00:02:00|561      |4575   |$14.57 |Swipe Transaction |67570      |Bettendorf     |IA            |52722.0|5311|null |
|7475329|2010-01-01 00:02:00|1129     |102    |$80.00 |Swipe Transaction |27092      |Vista          |CA            |92084.0|4829|null |
|7475331|2010-01-01 00:05:00|430      |2860   |$200.00|Swipe Transaction |27092      |Crown Point    |IN            |46307.0|4829|null |
|7475332|2010-01-01 00:06:00|848      |39

In [0]:
from pyspark.sql.functions import regexp_replace,col

In [0]:
transaction_amount_df = transaction_raw_df.withColumn("amount", regexp_replace(col("amount"), r"[$]" , "").cast('float')) \
    .withColumnRenamed("amount", "amount_dollar")

In [0]:
transaction_final_df = transaction_amount_df

In [0]:
transaction_final_df.show(100, truncate=False)

+-------+-------------------+---------+-------+-------------+------------------+-----------+-----------------+--------------+-------+----+-----+
|id     |date               |client_id|card_id|amount_dollar|use_chip          |Merchent_id|merchent_city    |merchent_state|zip    |mcc |error|
+-------+-------------------+---------+-------+-------------+------------------+-----------+-----------------+--------------+-------+----+-----+
|7475327|2010-01-01 00:01:00|1556     |2972   |-77.0        |Swipe Transaction |59935      |Beulah           |ND            |58523.0|5499|null |
|7475328|2010-01-01 00:02:00|561      |4575   |14.57        |Swipe Transaction |67570      |Bettendorf       |IA            |52722.0|5311|null |
|7475329|2010-01-01 00:02:00|1129     |102    |80.0         |Swipe Transaction |27092      |Vista            |CA            |92084.0|4829|null |
|7475331|2010-01-01 00:05:00|430      |2860   |200.0        |Swipe Transaction |27092      |Crown Point      |IN            |46307

In [0]:
mcc_schema = StructType([
    StructField("mcc_code",IntegerType()),
    StructField("Description", StringType())
])

In [0]:
mcc_raw_df = spark.read \
    .format("csv") \
        .schema(mcc_schema) \
        .load("dbfs:/FileStore/FinancialTransaction/mcc_raw")

In [0]:
mcc_final_df = mcc_raw_df

In [0]:
mcc_raw_df.show(truncate=False)

+--------+------------------------------------------+
|mcc_code|Description                               |
+--------+------------------------------------------+
|5812    |Eating Places and Restaurants             |
|5541    |Service Stations                          |
|7996    |Amusement Parks, Carnivals, Circuses      |
|5411    |Grocery Stores, Supermarkets              |
|4784    |Tolls and Bridge Fees                     |
|4900    |Utilities - Electric, Gas, Water, Sanitary|
|5942    |Book Stores                               |
|5814    |Fast Food Restaurants                     |
|4829    |Money Transfer                            |
|5311    |Department Stores                         |
|5211    |Lumber and Building Materials             |
|5310    |Discount Stores                           |
|3780    |Computer Network Services                 |
|5499    |Miscellaneous Food Stores                 |
|4121    |Taxicabs and Limousines                   |
|5300    |Wholesale Clubs   

In [0]:
mcc_raw_df.groupBy("Description").count().show(100,truncate=False)

+---------------------------------------------------+-----+
|Description                                        |count|
+---------------------------------------------------+-----+
|Cleaning and Maintenance Services                  |1    |
|Local and Suburban Commuter Transportation         |1    |
|Floor Covering Stores                              |1    |
|Grocery Stores, Supermarkets                       |1    |
|Books, Periodicals, Newspapers                     |1    |
|Wholesale Clubs                                    |1    |
|Podiatrists                                        |1    |
|Computer Network Services                          |1    |
|Heating, Plumbing, Air Conditioning Contractors    |1    |
|Tools, Parts, Supplies Manufacturing               |1    |
|Steel Drums and Barrels                            |1    |
|Miscellaneous Metals                               |1    |
|Cruise Lines                                       |1    |
|Leather Goods                          

In [0]:
cards_schema = StructType([
    StructField("id", IntegerType(), True),
    StructField("client_id", IntegerType(), True),
    StructField("card_brand", StringType(), True),
    StructField("card_type", StringType(), True),
    StructField("card_number", LongType(), True),
    StructField("card_expiry", StringType(), True),
    StructField("cvv", IntegerType(), True),
    StructField("has_chip", StringType(), True),
    StructField("num_cards_issued", IntegerType(), True),
    StructField("credit_limit", StringType(), True),
    StructField("acct_open_date", StringType(), True),
    StructField("year_pin_last_changed", IntegerType(), True),
    StructField("card_on_dark_web", StringType(), True)
])

In [0]:
cards_raw_df = spark.read \
    .format("csv") \
        .schema(cards_schema) \
        .load("dbfs:/FileStore/FinancialTransaction/cards_raw")

In [0]:
cards_raw_df.display()

id client_id card_brand card_type card_number card_expiry cvv has_chip num_cards_issued credit_limit acct_open_date year_pin_last_changed card_on_dark_web 4524 825 Visa Debit 4344676511950444 12/2022 623 YES 2 $24295 09/2002 2008 No 2731 825 Visa Debit 4956965974959986 12/2020 393 YES 2 $21968 04/2014 2014 No 3701 825 Visa Debit 4582313478255491 02/2024 719 YES 2 $46414 07/2003 2004 No 42 825 Visa Credit 4879494103069057 08/2024 693 NO 1 $12400 01/2003 2012 No 4659 825 Mastercard Debit (Prepaid) 5722874738736011 03/2009 75 YES 1 $28 09/2008 2009 No 4537 1746 Visa Credit 4404898874682993 09/2003 736 YES 1 $27500 09/2003 2012 No 1278 1746 Visa Debit 4001482973848631 07/2022 972 YES 2 $28508 02/2011 2011 No 3687 1746 Mastercard Debit 5627220683410948 06/2022 48 YES 2 $9022 07/2003 2015 No 3465 1746 Mastercard Debit (Prepaid) 5711382187309326 11/2020 722 YES 2 $54 06/2010 2015 No 3754 1746 Mastercard Debit (Prepaid) 5766121508358701 02/2023 908 YES 1 $99 07/2006 2012 No 5144 1718 Mastercard Debit 5495199163052054 03/2022 677 YES 2 $31599 10/2009 2009 No 2029 1718 Mastercard Debit 5804499644308599 07/2023 258 NO 2 $27480 03/2002 2008 No 2379 1718 Mastercard Debit 5766352389579834 02/2020 992 YES 1 $26743 03/2019 2019 No 2732 1718 Visa Debit 4242015583697294 06/2020 928 YES 1 $31463 04/2014 2014 No 4706 1718 Mastercard Debit 5191030913182493 06/2024 360 YES 1 $16055 09/2009 2009 No 281 708 Visa Credit 4017261190134817 05/2015 877 YES 2 $98100 01/2011 2011 No 1106 708 Mastercard Debit (Prepaid) 5581970288727991 06/2020 448 YES 1 $62 02/2007 2007 No 5621 708 Visa Debit 4032240655674503 06/2022 53 YES 1 $132439 11/2010 2011 No 5165 708 Visa Debit 4935974646456357 06/2020 649 YES 1 $125723 10/2009 2010 No 5757 1164 Mastercard Debit 5905027855347659 01/2022 886 YES 1 $34900 12/1999 2012 No 27 68 Visa Credit 4099623033306950 09/2021 74 YES 2 $9900 01/2002 2019 No 4648 68 Visa Debit 4281200324251212 07/2013 865 YES 2 $21587 09/2007 2007 No 5435 68 Visa Credit 4411456925570768 11/2022 922 YES 2 $15800 11/2005 2011 No 3287 1075 Mastercard Debit 5202477865497336 04/2022 861 YES 1 $29964 06/2005 2014 No 4761 1075 Mastercard Credit 5089768442116305 07/2023 686 YES 2 $11200 09/2010 2010 No 5286 1075 Mastercard Debit 5767339719294372 12/2021 669 NO 2 $26753 10/2014 2014 No 744 1711 Visa Debit 4595831603224644 05/2023 689 NO 2 $17480 01/2020 2020 No 5559 1116 Mastercard Debit 5341049613275152 09/2021 396 YES 2 $26546 11/2009 2009 No 4905 1116 Mastercard Debit 5668831527649353 01/2021 356 YES 1 $23253 09/2017 2017 No 79 1116 Visa Credit 4400056931148232 02/2021 497 YES 1 $16100 01/2005 2014 No 301 1116 Visa Credit 4808554251869440 02/2021 921 YES 2 $8700 01/2012 2012 No 3115 1116 Mastercard Debit 5224739362243611 01/2019 922 YES 1 $29333 05/2012 2012 No 3880 1752 Mastercard Debit 5294178176133532 07/2024 265 YES 2 $9496 07/2009 2012 No 1766 192 Visa Debit 4857799018106614 07/2021 930 YES 1 $25499 02/2020 2020 No 1767 192 Visa Debit 4324062360619923 02/2020 358 YES 1 $18641 02/2020 2020 No 745 640 Visa Debit 4852639114720724 05/2023 995 YES 1 $26019 01/2020 2020 No 1459 1679 Mastercard Debit 5656383455895230 01/2021 547 YES 1 $25845 02/2020 2020 No 138 1094 Visa Debit 4556928160477229 06/2023 64 YES 2 $2365 01/2007 2009 No 3755 1094 Mastercard Debit 5515782790823587 06/2023 419 YES 2 $18684 07/2006 2017 No 1768 1094 Visa Credit 4508388296516458 02/2021 364 NO 2 $7400 02/2020 2020 No 5924 1590 Mastercard Debit 5548265564669334 12/2024 145 YES 2 $4147 12/2008 2016 No 6074 1660 Visa Debit (Prepaid) 4986270376099447 04/2022 385 YES 1 $76 12/2012 2012 No 5923 1660 Discover Credit 6726060094896113 01/2009 105 NO 1 $4700 12/2008 2014 No 4223 1660 Visa Credit 4157109762296149 06/2021 433 YES 2 $5800 08/2007 2011 No 4455 1660 Mastercard Debit 5231462717450524 03/2024 754 YES 2 $12082 08/2016 2016 No 3234 1660 Mastercard Credit 5074836567307562 03/2023 741 NO 2 $6000 06/2002 2010 No 1005 1660 Visa Debit 4986369179342271 11/2009 367 YES 1 $620 02/2002 2014 No 

In [0]:
from pyspark.sql.functions import *

In [0]:
cards_date_df = cards_raw_df.withColumn("card_expiry", to_date(col("card_expiry"), "MM/yyyy").cast('date')) \
    .withColumn("acct_open_date", to_date(col("acct_open_date"), "MM/yyyy")) \
    .withColumn("acct_open_month", month(col("acct_open_date")).cast('int')) \
    .withColumn("acct_open_year", year(col("acct_open_date")).cast('int')) \
    .withColumn("credit_limit", regexp_replace(col("credit_limit"), r"[$]", "").cast('int')) \
    .withColumnRenamed("credit_limit", "credit_limit_dollar")

In [0]:
cards_date_df.display()

id client_id card_brand card_type card_number card_expiry cvv has_chip num_cards_issued credit_limit_dollar acct_open_date year_pin_last_changed card_on_dark_web acct_open_month acct_open_year 4524 825 Visa Debit 4344676511950444 2022-12-01 623 YES 2 24295 2002-09-01 2008 No 9 2002 2731 825 Visa Debit 4956965974959986 2020-12-01 393 YES 2 21968 2014-04-01 2014 No 4 2014 3701 825 Visa Debit 4582313478255491 2024-02-01 719 YES 2 46414 2003-07-01 2004 No 7 2003 42 825 Visa Credit 4879494103069057 2024-08-01 693 NO 1 12400 2003-01-01 2012 No 1 2003 4659 825 Mastercard Debit (Prepaid) 5722874738736011 2009-03-01 75 YES 1 28 2008-09-01 2009 No 9 2008 4537 1746 Visa Credit 4404898874682993 2003-09-01 736 YES 1 27500 2003-09-01 2012 No 9 2003 1278 1746 Visa Debit 4001482973848631 2022-07-01 972 YES 2 28508 2011-02-01 2011 No 2 2011 3687 1746 Mastercard Debit 5627220683410948 2022-06-01 48 YES 2 9022 2003-07-01 2015 No 7 2003 3465 1746 Mastercard Debit (Prepaid) 5711382187309326 2020-11-01 722 YES 2 54 2010-06-01 2015 No 6 2010 3754 1746 Mastercard Debit (Prepaid) 5766121508358701 2023-02-01 908 YES 1 99 2006-07-01 2012 No 7 2006 5144 1718 Mastercard Debit 5495199163052054 2022-03-01 677 YES 2 31599 2009-10-01 2009 No 10 2009 2029 1718 Mastercard Debit 5804499644308599 2023-07-01 258 NO 2 27480 2002-03-01 2008 No 3 2002 2379 1718 Mastercard Debit 5766352389579834 2020-02-01 992 YES 1 26743 2019-03-01 2019 No 3 2019 2732 1718 Visa Debit 4242015583697294 2020-06-01 928 YES 1 31463 2014-04-01 2014 No 4 2014 4706 1718 Mastercard Debit 5191030913182493 2024-06-01 360 YES 1 16055 2009-09-01 2009 No 9 2009 281 708 Visa Credit 4017261190134817 2015-05-01 877 YES 2 98100 2011-01-01 2011 No 1 2011 1106 708 Mastercard Debit (Prepaid) 5581970288727991 2020-06-01 448 YES 1 62 2007-02-01 2007 No 2 2007 5621 708 Visa Debit 4032240655674503 2022-06-01 53 YES 1 132439 2010-11-01 2011 No 11 2010 5165 708 Visa Debit 4935974646456357 2020-06-01 649 YES 1 125723 2009-10-01 2010 No 10 2009 5757 1164 Mastercard Debit 5905027855347659 2022-01-01 886 YES 1 34900 1999-12-01 2012 No 12 1999 27 68 Visa Credit 4099623033306950 2021-09-01 74 YES 2 9900 2002-01-01 2019 No 1 2002 4648 68 Visa Debit 4281200324251212 2013-07-01 865 YES 2 21587 2007-09-01 2007 No 9 2007 5435 68 Visa Credit 4411456925570768 2022-11-01 922 YES 2 15800 2005-11-01 2011 No 11 2005 3287 1075 Mastercard Debit 5202477865497336 2022-04-01 861 YES 1 29964 2005-06-01 2014 No 6 2005 4761 1075 Mastercard Credit 5089768442116305 2023-07-01 686 YES 2 11200 2010-09-01 2010 No 9 2010 5286 1075 Mastercard Debit 5767339719294372 2021-12-01 669 NO 2 26753 2014-10-01 2014 No 10 2014 744 1711 Visa Debit 4595831603224644 2023-05-01 689 NO 2 17480 2020-01-01 2020 No 1 2020 5559 1116 Mastercard Debit 5341049613275152 2021-09-01 396 YES 2 26546 2009-11-01 2009 No 11 2009 4905 1116 Mastercard Debit 5668831527649353 2021-01-01 356 YES 1 23253 2017-09-01 2017 No 9 2017 79 1116 Visa Credit 4400056931148232 2021-02-01 497 YES 1 16100 2005-01-01 2014 No 1 2005 301 1116 Visa Credit 4808554251869440 2021-02-01 921 YES 2 8700 2012-01-01 2012 No 1 2012 3115 1116 Mastercard Debit 5224739362243611 2019-01-01 922 YES 1 29333 2012-05-01 2012 No 5 2012 3880 1752 Mastercard Debit 5294178176133532 2024-07-01 265 YES 2 9496 2009-07-01 2012 No 7 2009 1766 192 Visa Debit 4857799018106614 2021-07-01 930 YES 1 25499 2020-02-01 2020 No 2 2020 1767 192 Visa Debit 4324062360619923 2020-02-01 358 YES 1 18641 2020-02-01 2020 No 2 2020 745 640 Visa Debit 4852639114720724 2023-05-01 995 YES 1 26019 2020-01-01 2020 No 1 2020 1459 1679 Mastercard Debit 5656383455895230 2021-01-01 547 YES 1 25845 2020-02-01 2020 No 2 2020 138 1094 Visa Debit 4556928160477229 2023-06-01 64 YES 2 2365 2007-01-01 2009 No 1 2007 3755 1094 Mastercard Debit 5515782790823587 2023-06-01 419 YES 2 18684 2006-07-01 2017 No 7 2006 1768 1094 Visa Credit 4508388296516458 2021-02-01 364 NO 2 7400 2020-02-01 2020 No 2 2020 5924 1590 Mastercard Debit 5548265564669334 2024-12-

In [0]:
cards_final_df = cards_date_df.drop("acct_open_date")

In [0]:
train_schema = StructType([
    StructField("trasaction_id", LongType()),
    StructField("is_fraud_label", StringType())
])

In [0]:
train_final_df = spark.read \
    .format("csv") \
        .schema(train_schema) \
        .load("dbfs:/FileStore/FinancialTransaction/train_raw")

In [0]:
train_final_df.show()

+-------------+--------------+
|trasaction_id|is_fraud_label|
+-------------+--------------+
|     10649266|            No|
|     23410063|            No|
|      9316588|            No|
|     12478022|            No|
|      9558530|            No|
|     12532830|            No|
|     19526714|            No|
|      9906964|            No|
|     13224888|            No|
|     13749094|            No|
|     12303776|            No|
|     19480376|            No|
|     11716050|            No|
|     20025400|            No|
|      7661688|            No|
|     16662807|            No|
|     21419778|            No|
|     18011186|            No|
|     23289598|            No|
|     11644547|            No|
+-------------+--------------+
only showing top 20 rows



In [0]:
user_df_schema = StructType([
    StructField("id", IntegerType(), True),
    StructField("current_age", IntegerType(), True),
    StructField("retirement_age", IntegerType(), True),
    StructField("birth_year", IntegerType(), True),
    StructField("birth_month", IntegerType(), True),
    StructField("gender", StringType(), True),
    StructField("address", StringType(), True),
    StructField("latitude", DoubleType(), True),
    StructField("longitude", DoubleType(), True),
    StructField("per_capita_income", StringType(), True),
    StructField("yearly_income", StringType(), True),
    StructField("total_debt", StringType(), True),
    StructField("credit_score", IntegerType(), True),
    StructField("num_credit_cards", IntegerType(), True)
])

In [0]:
user_df = spark.read \
    .format("csv") \
        .schema(user_df_schema) \
            .load("dbfs:/FileStore/FinancialTransaction/user_raw")

In [0]:
user_df.display()

id current_age retirement_age birth_year birth_month gender address latitude longitude per_capita_income yearly_income total_debt credit_score num_credit_cards 825 53 66 1966 11 Female 462 Rose Lane 34.15 -117.76 $29278 $59696 $127613 787 5 1746 53 68 1966 12 Female 3606 Federal Boulevard 40.76 -73.74 $37891 $77254 $191349 701 5 1718 81 67 1938 11 Female 766 Third Drive 34.02 -117.89 $22681 $33483 $196 698 5 708 63 63 1957 1 Female 3 Madison Street 40.71 -73.99 $163145 $249925 $202328 722 4 1164 43 70 1976 9 Male 9620 Valley Stream Drive 37.76 -122.44 $53797 $109687 $183855 675 1 68 42 70 1977 10 Male 58 Birch Lane 41.55 -90.6 $20599 $41997 $0 704 3 1075 36 67 1983 12 Female 5695 Fifth Street 38.22 -85.74 $25258 $51500 $102286 672 3 1711 26 67 1993 12 Male 1941 Ninth Street 45.51 -122.64 $26790 $54623 $114711 728 1 1116 81 66 1938 7 Female 11 Spruce Avenue 40.32 -75.32 $26273 $42509 $2895 755 5 1752 34 60 1986 1 Female 887 Grant Street 29.97 -92.12 $18730 $38190 $81262 810 1 192 27 66 1992 6 Male 888 Fifth Lane 38.65 -121.25 $27548 $56164 $15224 761 2 640 29 63 1990 9 Female 8677 Littlewood Lane 40.42 -104.74 $22427 $45727 $94016 629 1 1679 18 67 2002 1 Female 829 Fourth Boulevard 41.76 -71.48 $33914 $69149 $89214 776 1 1094 34 62 1985 10 Male 74786 Jefferson Drive 44.75 -85.6 $20325 $41442 $78833 712 3 1590 48 62 1971 5 Female 781 East Street 29.45 -98.5 $10059 $20513 $32509 599 1 1660 41 68 1978 4 Female 40 Washington Drive 36.73 -102.51 $11342 $23123 $5079 723 6 1747 54 71 1966 1 Male 3994 Hillside Drive 32.15 -94.79 $17898 $36497 $38333 719 6 153 76 71 1943 8 Female 172 Birch Street 35.29 -111.32 $21950 $27484 $16803 660 4 429 22 68 1997 11 Male 8145 Spruce Boulevard 35.19 -80.83 $26481 $53995 $89056 683 3 511 66 68 1953 10 Male 153 Tenth Lane 32.21 -110.88 $17460 $35602 $55369 661 5 309 28 57 1991 8 Male 2473 Lake Avenue 32.07 -82.91 $12321 $25122 $43205 819 3 777 18 65 2002 1 Male 970 Essex Drive 37.37 -122.21 $106305 $216740 $0 700 2 1946 76 66 1943 6 Male 9186 Washington Avenue 41.47 -81.67 $19524 $41109 $21486 698 2 1674 70 64 1949 4 Male 5073 Wessex Avenue 35.49 -90.35 $14172 $26858 $11245 712 2 482 45 65 1975 1 Male 195 Eighth Boulevard 42.39 -122.93 $17131 $34929 $63849 714 1 877 36 63 1983 8 Female 801 Mill Boulevard 33.44 -111.85 $16829 $34317 $61826 610 3 128 40 66 1979 4 Female 6914 Wessex Avenue 29.76 -95.38 $15389 $31377 $59615 722 2 775 37 58 1982 9 Male 776 Norfolk Boulevard 34.17 -118.46 $21402 $43638 $104052 627 1 1536 41 67 1978 11 Male 2015 Bayview Avenue 36.15 -85.5 $15955 $32531 $38260 766 2 140 37 72 1983 2 Female 108 Washington Street 36.28 -86.83 $20657 $42120 $72801 739 4 1884 18 64 2001 5 Male 660 Seventh Drive 39.98 -82.98 $28092 $57281 $89114 850 1 1874 49 66 1970 9 Male 7505 Tenth Boulevard 25.77 -80.2 $18828 $38390 $87923 783 4 1310 33 69 1986 9 Female 4930 Birch Drive 33.92 -78.02 $17498 $35670 $58182 751 2 1689 21 66 1998 9 Female 93 Plum Lane 41.29 -72.36 $30281 $61746 $154817 637 2 379 47 65 1972 11 Female 837 Lincoln Avenue 30.68 -88.04 $21331 $43496 $114563 765 3 34 41 55 1978 8 Male 7467 Spruce Drive 38.48 -121.34 $25431 $51854 $72162 737 2 822 51 68 1968 4 Female 6323 Sussex Boulevard 32.61 -117.03 $16942 $34540 $22641 793 5 1499 46 62 1973 11 Male 8738 Fourth Street 41.97 -88.14 $20248 $41287 $88151 662 1 1780 46 70 1973 10 Male 9344 Mill Drive 36.62 -121.82 $18663 $38054 $63293 666 1 1806 59 62 1961 2 Female 299 11th Street 42.31 -71.64 $39418 $80371 $108499 822 1 811 91 68 1929 2 Female 5492 Maple Drive 38.9 -94.68 $51642 $84694 $2149 741 7 1844 79 72 1941 2 Male 829 Birch Boulevard 27.8 -97.39 $23608 $37503 $14272 706 5 1852 57 75 1962 12 Male 41011 Seventh Boulevard 33.27 -111.94 $32056 $65357 $21844 685 4 1231 26 52 1994 1 Female 613 Little Creek Lane 26.41 -81.42 $10819 $22066 $38967 842 1 970 42 66 1977 11 Male 1942 Rose Avenue 29.1 -81.0 $21916 $44681 $42011 770 3 381 26 69 1994 2 Male 5101 Birch Lane 38.72 -90.47 $25163 $51306 $68198 675 1 1134 18 59 2002 2 Female 7 11th Dri

In [0]:
user_final_df = user_df.withColumn("per_capita_income", regexp_replace(col("per_capita_income"), r"[$]", "").cast('int')) \
    .withColumn("total_debt", regexp_replace(col("total_debt"), r"[$]", "").cast('int')) \
    .withColumn("yearly_income", regexp_replace(col("yearly_income"), r"[$]", "").cast('int')) \
    .withColumnRenamed("per_capita_income", "per_capita_income_dol") \
    .withColumnRenamed("total_debt", "total_debt_dol") \
    .withColumnRenamed("yearly_income", "yearly_income_dol")

In [0]:
user_final_df.display()

id current_age retirement_age birth_year birth_month gender address latitude longitude per_capita_income_dol yearly_income_dol total_debt_dol credit_score num_credit_cards 825 53 66 1966 11 Female 462 Rose Lane 34.15 -117.76 29278 59696 127613 787 5 1746 53 68 1966 12 Female 3606 Federal Boulevard 40.76 -73.74 37891 77254 191349 701 5 1718 81 67 1938 11 Female 766 Third Drive 34.02 -117.89 22681 33483 196 698 5 708 63 63 1957 1 Female 3 Madison Street 40.71 -73.99 163145 249925 202328 722 4 1164 43 70 1976 9 Male 9620 Valley Stream Drive 37.76 -122.44 53797 109687 183855 675 1 68 42 70 1977 10 Male 58 Birch Lane 41.55 -90.6 20599 41997 0 704 3 1075 36 67 1983 12 Female 5695 Fifth Street 38.22 -85.74 25258 51500 102286 672 3 1711 26 67 1993 12 Male 1941 Ninth Street 45.51 -122.64 26790 54623 114711 728 1 1116 81 66 1938 7 Female 11 Spruce Avenue 40.32 -75.32 26273 42509 2895 755 5 1752 34 60 1986 1 Female 887 Grant Street 29.97 -92.12 18730 38190 81262 810 1 192 27 66 1992 6 Male 888 Fifth Lane 38.65 -121.25 27548 56164 15224 761 2 640 29 63 1990 9 Female 8677 Littlewood Lane 40.42 -104.74 22427 45727 94016 629 1 1679 18 67 2002 1 Female 829 Fourth Boulevard 41.76 -71.48 33914 69149 89214 776 1 1094 34 62 1985 10 Male 74786 Jefferson Drive 44.75 -85.6 20325 41442 78833 712 3 1590 48 62 1971 5 Female 781 East Street 29.45 -98.5 10059 20513 32509 599 1 1660 41 68 1978 4 Female 40 Washington Drive 36.73 -102.51 11342 23123 5079 723 6 1747 54 71 1966 1 Male 3994 Hillside Drive 32.15 -94.79 17898 36497 38333 719 6 153 76 71 1943 8 Female 172 Birch Street 35.29 -111.32 21950 27484 16803 660 4 429 22 68 1997 11 Male 8145 Spruce Boulevard 35.19 -80.83 26481 53995 89056 683 3 511 66 68 1953 10 Male 153 Tenth Lane 32.21 -110.88 17460 35602 55369 661 5 309 28 57 1991 8 Male 2473 Lake Avenue 32.07 -82.91 12321 25122 43205 819 3 777 18 65 2002 1 Male 970 Essex Drive 37.37 -122.21 106305 216740 0 700 2 1946 76 66 1943 6 Male 9186 Washington Avenue 41.47 -81.67 19524 41109 21486 698 2 1674 70 64 1949 4 Male 5073 Wessex Avenue 35.49 -90.35 14172 26858 11245 712 2 482 45 65 1975 1 Male 195 Eighth Boulevard 42.39 -122.93 17131 34929 63849 714 1 877 36 63 1983 8 Female 801 Mill Boulevard 33.44 -111.85 16829 34317 61826 610 3 128 40 66 1979 4 Female 6914 Wessex Avenue 29.76 -95.38 15389 31377 59615 722 2 775 37 58 1982 9 Male 776 Norfolk Boulevard 34.17 -118.46 21402 43638 104052 627 1 1536 41 67 1978 11 Male 2015 Bayview Avenue 36.15 -85.5 15955 32531 38260 766 2 140 37 72 1983 2 Female 108 Washington Street 36.28 -86.83 20657 42120 72801 739 4 1884 18 64 2001 5 Male 660 Seventh Drive 39.98 -82.98 28092 57281 89114 850 1 1874 49 66 1970 9 Male 7505 Tenth Boulevard 25.77 -80.2 18828 38390 87923 783 4 1310 33 69 1986 9 Female 4930 Birch Drive 33.92 -78.02 17498 35670 58182 751 2 1689 21 66 1998 9 Female 93 Plum Lane 41.29 -72.36 30281 61746 154817 637 2 379 47 65 1972 11 Female 837 Lincoln Avenue 30.68 -88.04 21331 43496 114563 765 3 34 41 55 1978 8 Male 7467 Spruce Drive 38.48 -121.34 25431 51854 72162 737 2 822 51 68 1968 4 Female 6323 Sussex Boulevard 32.61 -117.03 16942 34540 22641 793 5 1499 46 62 1973 11 Male 8738 Fourth Street 41.97 -88.14 20248 41287 88151 662 1 1780 46 70 1973 10 Male 9344 Mill Drive 36.62 -121.82 18663 38054 63293 666 1 1806 59 62 1961 2 Female 299 11th Street 42.31 -71.64 39418 80371 108499 822 1 811 91 68 1929 2 Female 5492 Maple Drive 38.9 -94.68 51642 84694 2149 741 7 1844 79 72 1941 2 Male 829 Birch Boulevard 27.8 -97.39 23608 37503 14272 706 5 1852 57 75 1962 12 Male 41011 Seventh Boulevard 33.27 -111.94 32056 65357 21844 685 4 1231 26 52 1994 1 Female 613 Little Creek Lane 26.41 -81.42 10819 22066 38967 842 1 970 42 66 1977 11 Male 1942 Rose Avenue 29.1 -81.0 21916 44681 42011 770 3 381 26 69 1994 2 Male 5101 Birch Lane 38.72 -90.47 25163 51306 68198 675 1 1134 18 59 2002 2 Female 7 11th Drive 29.45 -98.5 12677 25847 46379 568 1 1296 60 64 1959 11 Female 2468 Spruce Drive 28.7 -81.34 22896 46683 93126 788 5 1880 61

Fraud Trasactions

In [0]:
transaction_final_df.createOrReplaceTempView("trasactions")

In [0]:
spark.sql("select count(*) from trasactions").show()

+--------+
|count(1)|
+--------+
|13305915|
+--------+



In [0]:
mcc_final_df.createOrReplaceTempView("mcc")

In [0]:
spark.sql("select count(*) from mcc").show()

+--------+
|count(1)|
+--------+
|     109|
+--------+



In [0]:
train_final_df.createOrReplaceTempView("trainlabels")

In [0]:
user_final_df.createOrReplaceTempView("users")

In [0]:
cards_final_df.createOrReplaceTempView("cards")

In [0]:
spark.sql("""SELECT count(*) FROM trasactions a
          JOIN mcc b on a.mcc == b.mcc_code """).show()

+--------+
|count(1)|
+--------+
|13305915|
+--------+



In [0]:
trans_df = spark.sql("""SELECT a.id as transaction_id,d.is_fraud_label,a.merchent_id,a.client_id as user_id, a.amount_dollar, a.use_chip,b.description,c.address as user_address from trasactions a
          JOIN mcc b on a.mcc == b.mcc_code
          JOIN users c on a.client_id == c.id
          JOIN trainlabels d on a.id == d.trasaction_id
          """)

In [0]:
Fraud_transaction_df = trans_df.withColumn("is_trasaction_fraud", when(col("is_fraud_label") == 'Yes', "Fraud Transaction").otherwise("Trasaction Done"))

In [0]:
Fraud_transaction_df.show()

+--------------+--------------+-----------+-------+-------------+------------------+--------------------+--------------------+-------------------+
|transaction_id|is_fraud_label|merchent_id|user_id|amount_dollar|          use_chip|         description|        user_address|is_trasaction_fraud|
+--------------+--------------+-----------+-------+-------------+------------------+--------------------+--------------------+-------------------+
|       7475341|            No|      33326|   1797|        43.33| Swipe Transaction|Taxicabs and Limo...|391 Martin Luther...|    Trasaction Done|
|       7475347|            No|      61195|    114|        -64.0| Swipe Transaction|    Service Stations|      112 Elm Avenue|    Trasaction Done|
|       7475363|            No|      81536|    285|          7.8| Swipe Transaction|     Discount Stores|       702 Elm Drive|    Trasaction Done|
|       7475378|            No|      29232|   1575|        17.14| Swipe Transaction|Taxicabs and Limo...|   23 12th Bo

In [0]:
Fraud_transaction_df.repartition(1) \
    .write \
        .format("csv") \
        .mode("overwrite") \
            .option("path", "dbfs:/FileStore/FinancialTransaction/transactionsdoneAndFraudCSV") \
                .save()

Creating external table on top of trsactions

In [0]:
spark.sql("CREATE DATABASE Financialtrasaction")

Out[127]: DataFrame[]

In [0]:
spark.sql("CREATE TABLE Financialtrasaction.trasactions (transaction_id INT,is_fraud_label VARCHAR(50),merchent_id INT,user_id INT,amount_dollar FLOAT,use_chip VARCHAR(50),description VARCHAR(100),user_address VARCHAR(150),is_trasaction_fraud VARCHAR(50)) USING CSV LOCATION 'dbfs:/FileStore/FinancialTransaction/transactionsdoneAndFraudCSV'")

Out[146]: DataFrame[]

In [0]:
spark.sql("DROP TABLE Financialtrasaction.trasactions")

Out[145]: DataFrame[]

In [0]:
spark.sql("SELECT * FROM Financialtrasaction.trasactions").show()

+--------------+--------------+-----------+-------+-------------+------------------+--------------------+--------------------+-------------------+
|transaction_id|is_fraud_label|merchent_id|user_id|amount_dollar|          use_chip|         description|        user_address|is_trasaction_fraud|
+--------------+--------------+-----------+-------+-------------+------------------+--------------------+--------------------+-------------------+
|       7475341|            No|      33326|   1797|        43.33| Swipe Transaction|Taxicabs and Limo...|391 Martin Luther...|    Trasaction Done|
|       7475347|            No|      61195|    114|        -64.0| Swipe Transaction|    Service Stations|      112 Elm Avenue|    Trasaction Done|
|       7475363|            No|      81536|    285|          7.8| Swipe Transaction|     Discount Stores|       702 Elm Drive|    Trasaction Done|
|       7475378|            No|      29232|   1575|        17.14| Swipe Transaction|Taxicabs and Limo...|   23 12th Bo

In [0]:
spark.sql("DESCRIBE EXTENDED Financialtrasaction.trasactions").show(50,truncate=False)

+----------------------------+----------------------------------------------------------------+-------+
|col_name                    |data_type                                                       |comment|
+----------------------------+----------------------------------------------------------------+-------+
|transaction_id              |int                                                             |null   |
|is_fraud_label              |varchar(50)                                                     |null   |
|merchent_id                 |int                                                             |null   |
|user_id                     |int                                                             |null   |
|amount_dollar               |float                                                           |null   |
|use_chip                    |varchar(50)                                                     |null   |
|description                 |varchar(100)                      

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-1869086002673465>:1
----> 1 host_name = dbutils.notebook.entry_point.getDbutils().notebook().getContext().tags().apply('Vikas')
      2 print(host_name)

File /databricks/spark/python/lib/py4j-0.10.9.5-src.zip/py4j/java_gateway.py:1321, in JavaMember.__call__(self, *args)
   1315 command = proto.CALL_COMMAND_NAME +\
   1316     self.command_header +\
   1317     args_command +\
   1318     proto.END_COMMAND_PART
   1320 answer = self.gateway_client.send_command(command)
-> 1321 return_value = get_return_value(
   1322     answer, self.gateway_client, self.target_id, self.name)
   1324 for temp_arg in temp_args:
   1325     temp_arg._detach()

File /databricks/spark/python/pyspark/errors/exceptions.py:228, in capture_sql_exception.<locals>.deco(*a, **kw)
    226 def deco(*a: Any, **kw: Any) -> Any:
    227     try:
--> 228 

Loan Risk